In [14]:
import speech_recognition as sr
import re
from collections import Counter
import math
import os
from sklearn.metrics.pairwise import cosine_similarity
import numpy as np

In [15]:
r = sr.Recognizer()

In [16]:
class args:
    fileDir = 'D:\\LuanVan\\LuanvanAPI\\nhacThuNghiem\\'
    fileNameResult = 'D:/LuanVan/LuanvanAPI/thuVienKetQua/AnhOiOlaiLyric'
    fileLyric = 'D:/LuanVan/LuanvanAPI/Lyric'
    numberOfSimilarSong = 3
    fileName = 'AnhOiOLai-ChiPuDatG_3'

In [17]:
opt = args()

In [18]:
filePath = opt.fileDir + opt.fileName +'.wav'

In [19]:
def checkDuration(filePath):
    with contextlib.closing(wave.open(filePath, 'r')) as fs:
        frames = fs.getnframes()
        rate = fs.getframerate()
        duration = frames/ float(rate)
        return(duration)

Chuyển file âm thanh thành text bằng thư viện Speech Recognition

In [20]:
def audioSpeechRecognitionByGoogle(filePath):
    with sr.AudioFile(filePath) as source:
        audio = r.record(source)
        
    try:
        temp = str(r.recognize_google(audio, language='vi-VN').lower())
        return temp
    
    except sr.UnknownValueError:
        print(filePath + " Google Speech Recognition could not understand audio")

 Lưu dữ liệu file text được chuyển vào một file tạm

In [21]:
filenameresult_ = opt.fileNameResult + '.txt'

# Open the file in append mode ('a') instead of write mode ('w+')
with open(filenameresult_, 'a', encoding='utf-8') as file:
    result = audioSpeechRecognitionByGoogle(filePath)
    file.write(result + '\n')  # Write the result followed by a newline character


Tìm file lời nhạc giống với file tạm trong thư viện lời bài hát bằng 
Cosine_similarity của thư viện sklearn

In [22]:
a_file = filenameresult_
b_file = ''
a_vals = Counter(a_file)
b_vals = Counter(b_file)
words  = list(a_vals.keys() | b_vals.keys())
a_vect = [a_vals.get(word, 0) for word in words]      
len_a  = sum(av*av for av in a_vect) ** 0.5                        

In [23]:
def testSimilarLyric(fileDir,features=[], song=[]):
    for fileSong in os.listdir(opt.fileLyric):
        f = os.path.join(fileDir, fileSong)
        if os.path.isfile(f):
            b_file = f
            b_vals = Counter(b_file)
            b_vect = [b_vals.get(word, 0) for word in words] 
            len_b  = sum(bv*bv for bv in b_vect) ** 0.5 
            dot    = sum(av*bv for av,bv in zip(a_vect, b_vect))  
            cosine = dot / (len_a * len_b)
            cosine_sim = cosine_similarity([a_vect], [b_vect])
            features.append(cosine)
            song.append(f)
            print("Cosine:", cosine)
            print(f)
             
        
features=[]
song=[]
testSimilarLyric(opt.fileLyric,features,song)

Cosine: 0.9546392394134904
D:/LuanVan/LuanvanAPI/Lyric\1Phut-Andiez.txt
Cosine: 0.9442314513443539
D:/LuanVan/LuanvanAPI/Lyric\AiLaNguoiThuongEm.txt
Cosine: 0.8944411488683947
D:/LuanVan/LuanvanAPI/Lyric\AlanWalkerxSteveAokixIsakOmarNoir-Lonely.txt
Cosine: 0.93290854431714
D:/LuanVan/LuanvanAPI/Lyric\AnhCuDiDi-HaRiWon.txt
Cosine: 0.9318581171840473
D:/LuanVan/LuanvanAPI/Lyric\BaoAnh-NhuLoiDon.txt
Cosine: 0.9272008304495992
D:/LuanVan/LuanvanAPI/Lyric\BichPhuong-BaoGioLayChong.txt
Cosine: 0.935608064396146
D:/LuanVan/LuanvanAPI/Lyric\BichPhuong-BuaYeu.txt
Cosine: 0.8856817688112084
D:/LuanVan/LuanvanAPI/Lyric\BichPhuong-DiDuDuaDi.txt
Cosine: 0.9001584418298703
D:/LuanVan/LuanvanAPI/Lyric\BichPhuong-EmBoHutThuocChua.txt
Cosine: 0.9274537597958579
D:/LuanVan/LuanvanAPI/Lyric\BichPhuong-GuiAnhXaNho.txt
Cosine: 0.9304425835611382
D:/LuanVan/LuanvanAPI/Lyric\BichPhuong-MinhYeuNhauDi.txt
Cosine: 0.9354720936668214
D:/LuanVan/LuanvanAPI/Lyric\CauHenCauThe.txt
Cosine: 0.9577466254715499
D:/Luan

Sắp xếp độ tương đồng từ cao đến thấp

In [24]:
a = []
def sortAscending(features):
 
    lenth = len(features)

    for i in range(0, lenth - 1):
        for j in range(i + 1, lenth):
            if (features[i] < features[j]):
                # Hoán đổi vị trí
                tmp = features[i]
                tmp2 = song[i]
                features[i] = features[j]
                song[i] = song[j]
                features[j] = tmp
                song[j] = tmp2
     
    #a = np.stack((features, song), axis = 1)
    return features, song


In [25]:
sortAscending(features)
a = np.stack((features, song), axis = 1)

ghi kết quả vào tệp văn bản

In [26]:
fileNameResult = "D:\\LuanVan\\LuanvanAPI\\thuVienKetQua\\ResultAnhOiOLai"+'_'+str(opt.numberOfSimilarSong)+".txt"
file = open(fileNameResult, 'a', encoding='utf-8')
file.writelines("Kết quả:"+'\n')
file.writelines(str(opt.numberOfSimilarSong) +' '+ " bài hát giống với file audio:" + opt.fileName +'\n')
file.writelines('-----------------------------------------------------------------------------------------------')
file.writelines("\n")
for i in range(0, opt.numberOfSimilarSong): 
    file.writelines(a[i])
    file.writelines("\n")
file.writelines('-----------------------------------------------------------------------------------------------')
file.writelines("\n")
file.close()

In [27]:
for i in range(0, opt.numberOfSimilarSong): 
    print(a[i])

['0.9598869691168703'
 'D:/LuanVan/LuanvanAPI/Lyric\\ViMeAnhBatChiaTay-MiuLe-7503053.txt']
['0.958223119258471' 'D:/LuanVan/LuanvanAPI/Lyric\\MasewxKhoiVu-AiNo.txt']
['0.9577466254715499' 'D:/LuanVan/LuanvanAPI/Lyric\\Chipu-AnhOiOLai.txt']


# Xay dung cau truc Inverted index

In [1]:
import nltk
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords
nltk.download('punkt')
nltk.download('stopwords')


[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\DucVo\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\DucVo\AppData\Roaming\nltk_data...
[nltk_data]   Unzipping corpora\stopwords.zip.


True

In [2]:
# Import thư viện os để làm việc với các tệp trong thư mục
import os

# Tạo danh sách để lưu trữ nội dung của tất cả các bài hát
all_lyrics = []

# Thư mục chứa các tệp lời bài hát
folder_path = 'D:\LuanVan\LuanvanAPI\Lyric'

# Lặp qua tất cả các tệp trong thư mục
for filename in os.listdir(folder_path):
    # Xác định đường dẫn đầy đủ của tệp
    file_path = os.path.join(folder_path, filename)
    
    # Đọc nội dung của tệp và lưu vào danh sách
    with open(file_path, 'r', encoding='utf-8') as file:
        lyrics = file.read()
        all_lyrics.append(lyrics)

# In nội dung của tất cả các bài hát
for i, lyrics in enumerate(all_lyrics, start=1):
    print(f"Lyrics for song {i}:")
    print(lyrics)
    print("-" * 20)


Lyrics for song 1:
Đã bao lâu lòng này anh chẳng nói
Nói với em ngàn lời anh cất giữ trong tim
Lần này đến lần khác đôi môi cứ lãng phí chẳng nói gì
Chỉ biết cạnh em dù cho em chẳng để ý
Và rồi em đã có người em yêu
Mỉm cười cho qua hết đi
Phải chăng là do người đến sau yêu em thật nhiều
Nói thay anh những lời anh mong ước
Và chúc cho em thật vui mặc anh bên lề của hạnh phúc
Một phút giây ta đã qua anh sẽ giữ như thước phim
Để khi nhớ em anh xem và ước rằng thực tế sẽ như vậy
Ở nơi đó thời gian như ngừng trôi hỡi em
Một phút đứng trước mặt em một phút là xa lời chưa nói
Một phút mạnh mẽ từ anh ta vẫn sẽ chung lối đi
Anh chẳng thể nào quay lại để bây giờ chẳng nói giá như
Giá như em hiểu rằng giá như em một lần nhìn được từ ánh mắt anh
Và giờ em đã có người em yêu
Mỉm cười cho qua hết đi
Phải chăng là do người đến sau yêu em thật nhiều
Nói thay anh những lời anh mong ước
Và chúc cho em thật vui mặc anh bên lề của hạnh phúc
Một phút giây ta đã qua anh sẽ giữ như thước phim
Để khi nhớ em 

In [3]:
import nltk
from nltk.tokenize import word_tokenize
import string

# Tiền xử lý dữ liệu cho từng lời bài hát trong danh sách all_lyrics
processed_lyrics_list = []

for lyrics in all_lyrics:
    # Tokenization
    tokens = word_tokenize(lyrics)
    
    # Loại bỏ dấu câu
    table = str.maketrans('', '', string.punctuation)
    tokens = [word.translate(table) for word in tokens]
    
    # Chuyển đổi thành chữ thường
    tokens = [word.lower() for word in tokens]
    
    # Xây dựng cụm từ từ 2 đến 3 chữ
    n_gram_sizes = [3, 8]
    n_grams = []
    for size in n_gram_sizes:
        n_grams.extend([' '.join(tokens[i:i+size]) for i in range(len(tokens) - size + 1)])
    
    # Kết hợp cả từng từ và cụm từ vào danh sách kết quả
    result = tokens + n_grams
    
    # Lưu trữ danh sách từ vựng đã xử lý cho lời bài hát hiện tại
    processed_lyrics_list.append(result)

# In danh sách từ vựng đã xử lý cho từng lời bài hát
for i, lyrics_tokens in enumerate(processed_lyrics_list, start=1):
    print(f"Processed lyrics for song {i}:")
    print(lyrics_tokens)
    print("-" * 20)


Processed lyrics for song 1:
['đã', 'bao', 'lâu', 'lòng', 'này', 'anh', 'chẳng', 'nói', 'nói', 'với', 'em', 'ngàn', 'lời', 'anh', 'cất', 'giữ', 'trong', 'tim', 'lần', 'này', 'đến', 'lần', 'khác', 'đôi', 'môi', 'cứ', 'lãng', 'phí', 'chẳng', 'nói', 'gì', 'chỉ', 'biết', 'cạnh', 'em', 'dù', 'cho', 'em', 'chẳng', 'để', 'ý', 'và', 'rồi', 'em', 'đã', 'có', 'người', 'em', 'yêu', 'mỉm', 'cười', 'cho', 'qua', 'hết', 'đi', 'phải', 'chăng', 'là', 'do', 'người', 'đến', 'sau', 'yêu', 'em', 'thật', 'nhiều', 'nói', 'thay', 'anh', 'những', 'lời', 'anh', 'mong', 'ước', 'và', 'chúc', 'cho', 'em', 'thật', 'vui', 'mặc', 'anh', 'bên', 'lề', 'của', 'hạnh', 'phúc', 'một', 'phút', 'giây', 'ta', 'đã', 'qua', 'anh', 'sẽ', 'giữ', 'như', 'thước', 'phim', 'để', 'khi', 'nhớ', 'em', 'anh', 'xem', 'và', 'ước', 'rằng', 'thực', 'tế', 'sẽ', 'như', 'vậy', 'ở', 'nơi', 'đó', 'thời', 'gian', 'như', 'ngừng', 'trôi', 'hỡi', 'em', 'một', 'phút', 'đứng', 'trước', 'mặt', 'em', 'một', 'phút', 'là', 'xa', 'lời', 'chưa', 'nói', 'một

In [4]:
import nltk
from nltk.corpus import stopwords
nltk.download('stopwords')

# Loại bỏ stop words và chuẩn hóa từ vựng cho từng lời bài hát trong danh sách processed_lyrics_list
stop_words = set(stopwords.words('vietnamese'))
processed_lyrics_list_no_stopwords = []

for lyrics_tokens in processed_lyrics_list:
    # Loại bỏ stop words
    lyrics_tokens_no_stopwords = [word for word in lyrics_tokens if word not in stop_words]
    
    # Lưu trữ danh sách từ vựng đã tiền xử lý (loại bỏ stop words) cho lời bài hát hiện tại
    processed_lyrics_list_no_stopwords.append(lyrics_tokens_no_stopwords)

# In danh sách từ vựng đã tiền xử lý (loại bỏ stop words) cho từng lời bài hát
for i, lyrics_tokens_no_stopwords in enumerate(processed_lyrics_list_no_stopwords, start=1):
    print(f"Processed lyrics (no stop words) for song {i}:")
    print(lyrics_tokens_no_stopwords)
    print("-" * 20)


[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\DucVo\AppData\Roaming\nltk_data...
[nltk_data]   Unzipping corpora\stopwords.zip.


Processed lyrics (no stop words) for song 1:
['bao', 'lâu', 'lòng', 'anh', 'chẳng', 'nói', 'nói', 'em', 'ngàn', 'lời', 'anh', 'cất', 'giữ', 'tim', 'lần', 'lần', 'khác', 'đôi', 'môi', 'cứ', 'lãng', 'phí', 'chẳng', 'nói', 'chỉ', 'biết', 'cạnh', 'em', 'dù', 'em', 'chẳng', 'ý', 'rồi', 'em', 'em', 'yêu', 'mỉm', 'cười', 'qua', 'hết', 'đi', 'phải', 'chăng', 'do', 'yêu', 'em', 'thật', 'nói', 'thay', 'anh', 'lời', 'anh', 'mong', 'ước', 'chúc', 'em', 'thật', 'vui', 'mặc', 'anh', 'bên', 'lề', 'hạnh', 'phúc', 'phút', 'giây', 'ta', 'qua', 'anh', 'sẽ', 'giữ', 'thước', 'phim', 'nhớ', 'em', 'anh', 'ước', 'rằng', 'thực', 'tế', 'sẽ', 'vậy', 'ở', 'nơi', 'thời', 'gian', 'ngừng', 'trôi', 'hỡi', 'em', 'phút', 'đứng', 'trước', 'mặt', 'em', 'phút', 'xa', 'lời', 'chưa', 'nói', 'phút', 'mạnh', 'mẽ', 'anh', 'ta', 'vẫn', 'sẽ', 'chung', 'lối', 'đi', 'anh', 'chẳng', 'thể', 'nào', 'quay', 'bây', 'giờ', 'chẳng', 'nói', 'giá', 'giá', 'em', 'hiểu', 'rằng', 'giá', 'em', 'lần', 'nhìn', 'ánh', 'mắt', 'anh', 'giờ', 'em', '

In [5]:
# Tích lũy các từ vựng duy nhất từ tất cả các bài hát
vocabulary = set()

for lyrics_tokens_no_stopwords in processed_lyrics_list_no_stopwords:
    # Thêm các từ vựng trong lời bài hát vào tập hợp vocabulary
    vocabulary.update(lyrics_tokens_no_stopwords)

# Chuyển đổi tập hợp vocabulary thành danh sách
vocabulary_list = list(vocabulary)

# In danh sách từ vựng chung
print("Vocabulary:")
print(vocabulary_list)


Vocabulary:
['', 'tên là muộn phiền nên làm sao dám', 'người dưng  chỉ là ngừng yêu mà', 'vùi mình vào', 'lại', ' đến mức', ' chỉ có', 'người vì sao', 'em thật nhiều', 'không còn heo', 'đôi sao chẳng số phu thê em ơi', 'thật là dài', 'theo một tình', 'bước ai xa', 'những hy vọng tháng ngày rồi trôi đi', 'mơ  wake up  i m wake', 'bình và mong', 'yêu rồi khoảnh', ' một cuộc sống dâng dâng dâng ', 'anh ở nhà nếu mai cách xa liệu', 'anh đây một ngày em có bước đi', ' làm dù', 'we made and', 'nghĩ quá khó', 'dấn bước trên', 'biệt li  cánh hoa rụng rơi phận', 'xì luôn nghỉ chơi đừng cò quay khiến', 'đường về thì dài mà lòng thì như', 'đau về anh được chôn dấu my baby', 'như beyoncé hát', 'á ” hình như em cần vitamin a', 'qua nỗi buồn', 'manh đưa trái tim tôi hát ca vang', 'em vẫn chờ nơi ấy yêu xa khó', ' tình yêu vỡ tan cứ quay đầu', 'nhau  vội', 'bật', 'giả', 'lẽ yêu ', 'vấp ngã trên đời thay đổi nhìn về', 'bề dáng ai về chung lối người mang', 'của hạnh phúc một phút giây ta đã', '

In [8]:
# Xây dựng inverted index
inverted_index = {}

# Duyệt qua danh sách từ vựng
for word in vocabulary_list:
    # Khởi tạo danh sách các bài hát chứa từ vựng
    song_indices = []
    
    # Duyệt qua danh sách các lời bài hát đã được tiền xử lý
    for i, lyrics_tokens_no_stopwords in enumerate(processed_lyrics_list_no_stopwords):
        # Nếu từ vựng có trong danh sách của lời bài hát hiện tại, thêm chỉ số của bài hát vào danh sách song_indices
        if word in lyrics_tokens_no_stopwords:
            song_indices.append(i)
    
    # Lưu trữ từ vựng và danh sách chỉ số bài hát vào inverted index
    inverted_index[word] = song_indices

# In inverted index
print("Inverted index:")
print(inverted_index)


Inverted index:
{'': [0, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50, 51, 52, 53, 54, 55, 57, 58, 59, 60, 62, 63, 64, 65, 66, 67, 68, 69, 71, 72, 73, 74, 75, 76, 77, 78, 79, 80, 81, 82, 83, 84, 85, 86, 87, 88, 89, 90, 91, 92, 94, 96, 97, 98, 99, 102, 103, 104], 'tên là muộn phiền nên làm sao dám': [72], 'người dưng  chỉ là ngừng yêu mà': [28], 'vùi mình vào': [38], 'lại': [21, 64, 79, 104], ' đến mức': [21], ' chỉ có': [46], 'người vì sao': [48], 'em thật nhiều': [0], 'không còn heo': [4], 'đôi sao chẳng số phu thê em ơi': [50], 'thật là dài': [75], 'theo một tình': [48], 'bước ai xa': [89], 'những hy vọng tháng ngày rồi trôi đi': [68], 'mơ  wake up  i m wake': [44], 'bình và mong': [64], 'yêu rồi khoảnh': [68], ' một cuộc sống dâng dâng dâng ': [88], 'anh ở nhà nếu mai cách xa liệu': [33], 'anh đây một ngày em có bước đi': [100], ' làm dù'

In [9]:
import json

# Lưu trữ inverted index vào tệp JSON
with open('inverted_index.json', 'w') as json_file:
    json.dump(inverted_index, json_file)


In [10]:
import os

current_directory = os.getcwd()
print("Current directory:", current_directory)


Current directory: C:\Users\DucVo\anaconda3\envs\Luanvan


Thực hiện truy vấn để tìm kiếm các bài hát phù hợp:

In [19]:
# Xây dựng inverted index với TF-IDF
inverted_index_tf_idf = {}

for word in vocabulary_list:
    # Khởi tạo danh sách các bài hát chứa từ vựng và giá trị TF-IDF
    song_tf_idf_pairs = []
    
    # Duyệt qua danh sách các lời bài hát đã được tiền xử lý
    for i, lyrics_tokens_no_stopwords in enumerate(processed_lyrics_list_no_stopwords):
        # Nếu từ vựng có trong danh sách của lời bài hát hiện tại, tính giá trị TF-IDF và thêm vào danh sách song_tf_idf_pairs
        if word in lyrics_tokens_no_stopwords:
            tf_idf = calculate_tf_idf(word, lyrics_tokens_no_stopwords, idf_scores)
            song_tf_idf_pairs.append((i, tf_idf))
    
    # Lưu trữ từ vựng và danh sách (chỉ số bài hát, giá trị TF-IDF) vào inverted index
    inverted_index_tf_idf[word] = song_tf_idf_pairs

# Hàm thực hiện truy vấn sử dụng TF-IDF
def search_with_tf_idf(query, idf_scores, inverted_index):
    query_tokens = word_tokenize(query)
    query_tokens = [word.lower() for word in query_tokens if word.lower() not in stop_words]

    matching_songs = set()
    for token in query_tokens:
        if token in inverted_index:
            for song_index, tf_idf in inverted_index[token]:
                matching_songs.add(song_index)

    return matching_songs

# Người dùng nhập truy vấn
user_query = "Người ta thường nói, đừng nên quá yêu một ai"

# Thực hiện truy vấn với TF-IDF
result_with_tf_idf = search_with_tf_idf(user_query, idf_scores, inverted_index_tf_idf)

# In kết quả
print("Matching songs with TF-IDF:")
max_results = 10  # Giới hạn số lượng kết quả hiển thị
for i, song_index in enumerate(result_with_tf_idf):
    if i >= max_results:
        break
    print(f"Song {song_index + 1}")



Matching songs with TF-IDF:
Song 1
Song 2
Song 4
Song 5
Song 6
Song 7
Song 8
Song 9
Song 10
Song 11


#################################################################

In [21]:
import os

file_names = []

for filename in os.listdir(folder_path):
    file_names.append(filename)

# Xây dựng inverted index với TF-IDF
inverted_index_tf_idf = {}

for word in vocabulary_list:
    # Khởi tạo danh sách các bài hát chứa từ vựng và giá trị TF-IDF
    song_tf_idf_pairs = []
    
    # Duyệt qua danh sách các lời bài hát đã được tiền xử lý
    for i, lyrics_tokens_no_stopwords in enumerate(processed_lyrics_list_no_stopwords):
        # Nếu từ vựng có trong danh sách của lời bài hát hiện tại, tính giá trị TF-IDF và thêm vào danh sách song_tf_idf_pairs
        if word in lyrics_tokens_no_stopwords:
            tf_idf = calculate_tf_idf(word, lyrics_tokens_no_stopwords, idf_scores)
            song_tf_idf_pairs.append((i, tf_idf))
    
    # Lưu trữ từ vựng và danh sách (chỉ số bài hát, giá trị TF-IDF) vào inverted index
    inverted_index_tf_idf[word] = song_tf_idf_pairs

# Hàm thực hiện truy vấn sử dụng TF-IDF
def search_with_tf_idf(query, idf_scores, inverted_index):
    query_tokens = word_tokenize(query)
    query_tokens = [word.lower() for word in query_tokens if word.lower() not in stop_words]

    matching_songs = set()
    for token in query_tokens:
        if token in inverted_index:
            for song_index, tf_idf in inverted_index[token]:
                matching_songs.add(song_index)

    return matching_songs

# Người dùng nhập truy vấn
user_query = "Tìm về kí ức cố xóa đi đoạn tình ban sơ Rồi lại chơ vơ đứng giữa nơi đại lộ tan vỡ Mãi chìm đắm trong lầm lỡ"

# Thực hiện truy vấn với TF-IDF
result_with_tf_idf = search_with_tf_idf(user_query, idf_scores, inverted_index_tf_idf)

# In kết quả
print("Matching songs with TF-IDF:")
for song_index in result_with_tf_idf:
    file_name = file_names[song_index]  # Lấy tên tệp từ danh sách file_names
    print(f"Song in file: {file_name}")




Matching songs with TF-IDF:
Song in file: 1Phut-Andiez.txt
Song in file: AiLaNguoiThuongEm.txt
Song in file: AnhCuDiDi-HaRiWon.txt
Song in file: BaoAnh-NhuLoiDon.txt
Song in file: BichPhuong-BaoGioLayChong.txt
Song in file: BichPhuong-BuaYeu.txt
Song in file: BichPhuong-DiDuDuaDi.txt
Song in file: BichPhuong-EmBoHutThuocChua.txt
Song in file: BichPhuong-GuiAnhXaNho.txt
Song in file: BichPhuong-MinhYeuNhauDi.txt
Song in file: CauHenCauThe.txt
Song in file: Chipu-AnhOiOLai.txt
Song in file: ChiPu-ChiTaBietThoi.txt
Song in file: ChiPu-DoaHoaHong.txt
Song in file: ChiPu-TalkToMeCoNenDungLai.txt
Song in file: ChungTaKhongThuocveNhau.txt
Song in file: DamVinhHung-Hello.txt
Song in file: DatGxDuUyen-BanhMiKhong.txt
Song in file: DatTGNgocxHaleyyxMasew-DieuKhacLa.txt
Song in file: DongNhi-Badboy.txt
Song in file: DucPhuc-QuaKhuDoiHienTaiDon.txt
Song in file: DucPhucHetThuongCanNho.txt
Song in file: DuongMotChieu-HuynhTuMagazine-4855398.txt
Song in file: EddyKien-HatChoEmNgheMoiNgay.txt
Song in

In [22]:
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity

# Biểu diễn văn bản bằng vector TF-IDF
vectorizer = TfidfVectorizer()
tfidf_matrix = vectorizer.fit_transform(all_lyrics)

# Biểu diễn văn bản truy vấn
query_vector = vectorizer.transform([user_query])

# Tính cosine similarity
cosine_similarities = cosine_similarity(query_vector, tfidf_matrix).flatten()

# Sắp xếp kết quả theo cosine similarity
sorted_results = sorted(range(len(cosine_similarities)), key=lambda i: cosine_similarities[i], reverse=True)

# In ra top kết quả
top_k = 3
print(f"Top {top_k} matching songs with Cosine Similarity:")
for idx in sorted_results[:top_k]:
    print(f"Song {idx + 1} - Cosine Similarity: {cosine_similarities[idx]}")


Top 3 matching songs with Cosine Similarity:
Song 30 - Cosine Similarity: 0.5019216386352413
Song 85 - Cosine Similarity: 0.1592071308891142
Song 54 - Cosine Similarity: 0.12638333179099903
